<a href="https://colab.research.google.com/github/iued-uni-heidelberg/compling2021/blob/main/Session04WordVectorsSpanish.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Word Vectors

Presentations [slides](intro-word-vectors-DAAD-2021-v22.pdf); Original [slides](word-vectors.pdf)

Word vectors (also known as 'word embeddings') are one of the most popular kinds of AI models. They are extremely useful in many domains. In essence, a word vector is a set of numbers that attempt to capture the meaning of a word. In typical implementations, each word is represented by a set of 200-300 numbers. In linear algebra, a one-dimensional array of numbers is known as a 'vector', hence these sets of numbers representing words' meanings are known as 'word vectors'.

Using neural networks, we can expose the computer to a large amount of text, and allow it to learn an appropriate set of numbers for each word it encounters. In this notebook, we will learn about the most famous of all word vector algorithms, `word2vec`, which was first described by Tomas Mikolov and his team in 2013:

* Tomas Mikolov, Ilya Sutskever, and others, ‘Distributed Representations of Words and Phrases and Their Compositionality’, in Advances in Neural Information Processing Systems 26, ed. by C. J. C. Burges and others (Curran Associates, Inc., 2013), pp. 3111–19 <http://papers.nips.cc/paper/5021-distributed-representations-of-words-and-phrases-and-their-compositionality.pdf>
* Tomas Mikolov, Kai Chen, and others, ‘Efficient Estimation of Word Representations in Vector Space’, ArXiv:1301.3781 Cs, 2013 <http://arxiv.org/abs/1301.3781>.

In fact, `word2vec` is not a single algorithm, but rather a family of similar algorithms. In this session we will consider just the most famous `word2vec` algorithm, namely the `skip-gram model` trained using `negative sampling`.

## Applications of Word Vectors

Word vectors allow the computer to 'understand' language far more effectively. Rather than seeing each word as simply an arbitrarily different object, a computer using word vectors can analyse each word as a point in 200- or 300-dimenstional space. Words that are similar in meaning will have similar word vectors. And as we will see, the spaces between the word vectors are also significant: the words are arranged in patterns that represent their relationships to one another.

Accordingly, most AI systems that process language now include a word vector layer as part of their architecure. When the system encounters some text (e.g. when you speak to Siri or Alexa), your words are converted into word vectors, *and then* the computer examines what the text says and determines how it should respond.

In the Humanities, word vectors have become a popular modelling tool, because they allow researchers to perform sophisticated analysis on large corpora of text. Some examples include:

* [The Women Writers Vector Toolkit](https://wwp.northeastern.edu/lab/wwvt/index.html)
* William L. Hamilton, Jure Leskovec, and Dan Jurafsky, ‘Diachronic Word Embeddings Reveal Statistical Laws of Semantic Change’, ArXiv:1605.09096 [Cs], 2018 <http://arxiv.org/abs/1605.09096>.
* Ryan Heuser, 'Semantic Networks' <https://ryanheuser.org/word-vectors-4/>

## Training an English `word2vec` model in Gensim

It is very easy to train a `word2vec` model in Gensim, which includes Mikolov's original `word2vec` code in its codebase.

In [ ]:
from gensim.models import Word2Vec # The word2vec model class
import gensim.downloader as api # Allows us to download some free training data
corpus = api.load('text8')
# api.info()

[==================================================] 100.0% 31.6/31.6MB downloaded


text8 is first 100MB from English wikipedia, 17 million words

The file is downloadable from 
http://mattmahoney.net/dc/text8.zip


In [ ]:
# Examine the corpus to see what is there
api.info("text8")

{'checksum': '68799af40b6bda07dfa47a32612e5364',
 'description': 'First 100,000,000 bytes of plain text from Wikipedia. Used for testing purposes; see wiki-english-* for proper full Wikipedia datasets.',
 'file_name': 'text8.gz',
 'file_size': 33182058,
 'license': 'not found',
 'num_records': 1701,
 'parts': 1,
 'read_more': ['http://mattmahoney.net/dc/textdata.html'],
 'reader_code': 'https://github.com/RaRe-Technologies/gensim-data/releases/download/text8/__init__.py',
 'record_format': 'list of str (tokens)'}

In [ ]:
type(corpus)

text8.Dataset

### Step 1: Set hyperparameters and instantiate model

In [ ]:
vector_size = 100 # Dimensionality of the word vectors
window = 5 # How many words either side? (5 = 5 context words either side, i.e. 10 context words in total)
use_skip_gram = 1 # If you set this to 0, then it will create a 'continuous bag of words' model instead
use_softmax = 0 # If you set this to 1, then hierarchical softmax will be used instead of negative sampling
negative_samples = 5 # How many incorrect answers to generate per correct answer when negative sampling

model = Word2Vec(
    size=vector_size,
    window=window,
    sg=use_skip_gram,
    hs=use_softmax,
    negative=negative_samples
)

### Step 2: Fit model to corpus

In [ ]:
# build a model
model.build_vocab(corpus)

In [ ]:
# Train the model on the corpus
model.train(sentences=corpus, epochs=5, total_examples=model.corpus_count)

(62533475, 85026035)

### Step 3: Extract word vectors from model

The fully trained model includes all of the weights used to predict the context words for each input word. If you are not planning on training the model further, these weights can be discarded, and you can just keep the weights for the word vectors.

In [ ]:
word_vectors = model.wv
del model # Delete the whole model to free up the computer's RAM

### Step 4: Have a play with the model

There are several ways you can use word vectors. One of the most famous is to use them to compute analogies. The formula is:

<center><em>x</em> is to <em>small</em> as <em>biggest</em> is to <em>big</em></center>

$$x - vector('small') = vector('biggest') - vector('big')$$

$$\therefore x = vector('small') + vector('biggest') - vector('big')$$

In [ ]:
# See the word vector for a particular word
vector = word_vectors['banana']
print(vector)

In [ ]:
# See which words are closest to a given word in the vector space
similar_words = word_vectors.most_similar('university', topn=10)
print('\n'.join([str(tup) for tup in similar_words]))

In [ ]:
# See which words are closest to a given word in the vector space
similar_words = word_vectors.most_similar('red', topn=10)
print('\n'.join([str(tup) for tup in similar_words]))

In [ ]:
# See which words are closest to a given word in the vector space
similar_words = word_vectors.most_similar('brussels', topn=10)
print('\n'.join([str(tup) for tup in similar_words]))

In [ ]:
# See which words are closest to a given word in the vector space
similar_words = word_vectors.most_similar('germany', topn=10)
print('\n'.join([str(tup) for tup in similar_words]))

In [ ]:
# See which words are closest to a given word in the vector space
similar_words = word_vectors.most_similar('strange', topn=10)
print('\n'.join([str(tup) for tup in similar_words]))

In [ ]:
# Compute analogous words
# E.g. x is to queen as man is to king => x = v('queen') + v('man') - v('king')
analogous_words = word_vectors.most_similar(negative=['man'], positive=['king','woman'])
print('\n'.join([str(tup) for tup in analogous_words]))

In [ ]:
# Compute analogous words
# E.g. x is to queen as man is to king => x = v('queen') + v('man') - v('king')
analogous_words = word_vectors.most_similar(negative=['king'], positive=['queen','man'])
print('\n'.join([str(tup) for tup in analogous_words]))

In [ ]:
# Compute analogous words
# E.g. x is to queen as man is to king => x = v('queen') + v('man') - v('king')
analogous_words = word_vectors.most_similar(negative=['mother'], positive=['father','daughter'])
print('\n'.join([str(tup) for tup in analogous_words]))

In [ ]:
# Compute analogous words
# E.g. x is to queen as man is to king => x = v('queen') + v('man') - v('king')
analogous_words = word_vectors.most_similar(negative=['mother'], positive=['father','girl'])
print('\n'.join([str(tup) for tup in analogous_words]))

In [ ]:
# Compute analogous words
# x is to daughter as people is to person (plural + daughter)
analogous_words = word_vectors.most_similar(negative=['person'], positive=['people','daughter'])
print('\n'.join([str(tup) for tup in analogous_words]))

In [ ]:
analogous_words = word_vectors.most_similar(negative=['soft'], positive=['hard','softest'])
print('\n'.join([str(tup) for tup in analogous_words]))

In [ ]:
# try your own examples... 

## Step 5. Training the Spanish model

Now let's train a model on our own corpus.

Spanish, Armenian, Ukrainian, Russian plaintext wikipedias are available at:
https://lindat.mff.cuni.cz/repository/xmlui/handle/11234/1-2735#

The small Spanish model is trained on ~35MW corpus (training time ~20 min)

(Or we can use the same size ~15 Million Words, (100MB) of these corpora to make sure the model is built within a reasonable time; however, when you have more time, you can try a more complete corpus).

The large Spanish model is trained on ~100MW corpus (training time ~ 50 min)

It is possible to download/unzip/upload the files manually, however, it is faster to automatically load them directly from Heidelberg server space https://heibox.uni-heidelberg.de/d/42a07c9e95774e099a81/  into your colab environment. 



In [ ]:
!rm /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt
!rm index.html?dl=1

rm: cannot remove '/usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt': No such file or directory
rm: cannot remove 'index.html?dl=1': No such file or directory


### Either: 5a Spanish medium (~20 min training time)

In [ ]:
!wget https://heibox.uni-heidelberg.de/f/254c7835b1e9449e92d8/?dl=1

In [ ]:
!cp index.html?dl=1 /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt

In [ ]:
!head --lines=15 /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt

### Or: 5b Spanish large (~50 min training time)

In [ ]:
!wget https://heibox.uni-heidelberg.de/f/22505f6ee8404234a479/?dl=1

In [ ]:
!cp index.html?dl=1 /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt

In [ ]:
!head --lines=15 /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt

### Or: 5c Spanish small (~10 min training time)

In [ ]:
!wget 

In [ ]:
!cp index.html?dl=1 /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt

In [ ]:
!head --lines=15 /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt

### Or: 5d French

In [ ]:
!wget https://heibox.uni-heidelberg.de/f/5cdb485efd4046f2a457/?dl=1

In [ ]:
!cp index.html?dl=1 /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt

In [ ]:
!head --lines=15 /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt

### Or: 5e Russian

In [ ]:
!wget https://heibox.uni-heidelberg.de/f/d8d381152ceb479080ca/?dl=1

In [ ]:
!cp index.html?dl=1 /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt

In [ ]:
!head --lines=15 /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt

### Or: 5f Georgian

In [ ]:
!wget https://heibox.uni-heidelberg.de/f/fa3509d869b949459f91/?dl=1

Lemmatized corpus

In [ ]:
!wget https://heibox.uni-heidelberg.de/f/b381c458ad5e4773a77d/?dl=1

--2021-09-03 08:53:16--  https://heibox.uni-heidelberg.de/f/b381c458ad5e4773a77d/?dl=1
Resolving heibox.uni-heidelberg.de (heibox.uni-heidelberg.de)... 129.206.7.113
Connecting to heibox.uni-heidelberg.de (heibox.uni-heidelberg.de)|129.206.7.113|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://heibox.uni-heidelberg.de/seafhttp/files/7b521159-dc90-4e0f-89fa-6876b167b9fb/ka_lem.txt [following]
--2021-09-03 08:53:16--  https://heibox.uni-heidelberg.de/seafhttp/files/7b521159-dc90-4e0f-89fa-6876b167b9fb/ka_lem.txt
Reusing existing connection to heibox.uni-heidelberg.de:443.
HTTP request sent, awaiting response... 200 OK
Length: 329202500 (314M) [text/plain]
Saving to: ‘index.html?dl=1’

index.html?dl=1     100%[===================>] 313.95M  14.9MB/s    in 21s     

2021-09-03 08:53:37 (15.2 MB/s) - ‘index.html?dl=1’ saved [329202500/329202500]



In [ ]:
!cp index.html?dl=1 wiki_geo_lem.txt

In [ ]:
!head --lines=10 wiki_geo_lem.txt

ედუარდი
შევარდნაძე
ედუარდი
ამბროსის
ძე
შევარდნაძე
(
დ
.
25


In [ ]:
FIn = open("wiki_geo_lem.txt", 'r')
FOut = open('wiki_geo_l.txt', 'w')

i = 0
for SLine in FIn:
  i = i + 1
  SLine = SLine.strip() + ' '
  if i % 10000 == 0:
    SLine += '\n'
  
  FOut.write(SLine)

FOut.flush()
FOut.close()


In [ ]:
!head --lines=10 wiki_geo_l.txt

ედუარდი შევარდნაძე ედუარდი ამბროსის ძე შევარდნაძე ( დ . 25 იანვარი , @card@ , მამათი , დღევანდელი ლანჩხუთის მუნიციპალიტეტი — გ . @card@ ივლისი , 2014 , თბილისი ) — ქართველი პოლიტიკოსი და სახელმწიფო მოღვაწე . @card@ წელი საბჭო კავშირი საგარეო საქმე მინისტრი , @card@ წელი საქართველო პრეზიდენტი . სკკპ წევრი @card@ წელი . @card@ წელი ივლის-ოქტომბერში მუშაობს საქართველო ალკკ თბილისი ორჯონიკიძის რაიკომი ინსტრუქტორად . IX-XI მოწვევების უმაღლესი საბჭო დეპუტატი . სოციალისტური შრომა გმირი ( @card@ ) . სკკპ ცკ-ის პოლიტბიუროს წევრობა კანდიდატი ( @card@ ) , წევრი 1985 წელი ივლისი . @card@ წელი არის საქართველო სსრ-ის კომკავშირის პირველი მდივანი , @card@ წელი კომპარტიის მცხეთის რაიონული კომიტეტი პირველი მდივანი , ხოლო შემდეგ თბილისი პირველი მაისი რაიონი რაიკომი მდივანი . @card@ წელი არის კომპარტიის ცენტრალური კომიტეტი წევრი . @card@ წელი არის საზოგადოებრივი წესრიგი დაცვა მინისტრი მოადგილე . @card@ წელი საქართველო სსრ შინაგანი საქმე მინისტრი . @card@ წელი აირჩევს საქართველო კომპარტიის ცკ-ის პირველი მდ

In [ ]:
!wc wiki_geo_lem.txt

 18054750  18054749 329202500 wiki_geo_lem.txt


In [ ]:
!cp index.html?dl=1 /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt

Alternatively, copy lemmatized corpus

In [ ]:
!cp wiki_geo_l.txt /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt

In [ ]:
!head --lines=15 /usr/local/lib/python3.7/dist-packages/gensim/test/test_data/myOwnLangText8.txt

ედუარდი შევარდნაძე ედუარდი ამბროსის ძე შევარდნაძე ( დ . 25 იანვარი , @card@ , მამათი , დღევანდელი ლანჩხუთის მუნიციპალიტეტი — გ . @card@ ივლისი , 2014 , თბილისი ) — ქართველი პოლიტიკოსი და სახელმწიფო მოღვაწე . @card@ წელი საბჭო კავშირი საგარეო საქმე მინისტრი , @card@ წელი საქართველო პრეზიდენტი . სკკპ წევრი @card@ წელი . @card@ წელი ივლის-ოქტომბერში მუშაობს საქართველო ალკკ თბილისი ორჯონიკიძის რაიკომი ინსტრუქტორად . IX-XI მოწვევების უმაღლესი საბჭო დეპუტატი . სოციალისტური შრომა გმირი ( @card@ ) . სკკპ ცკ-ის პოლიტბიუროს წევრობა კანდიდატი ( @card@ ) , წევრი 1985 წელი ივლისი . @card@ წელი არის საქართველო სსრ-ის კომკავშირის პირველი მდივანი , @card@ წელი კომპარტიის მცხეთის რაიონული კომიტეტი პირველი მდივანი , ხოლო შემდეგ თბილისი პირველი მაისი რაიონი რაიკომი მდივანი . @card@ წელი არის კომპარტიის ცენტრალური კომიტეტი წევრი . @card@ წელი არის საზოგადოებრივი წესრიგი დაცვა მინისტრი მოადგილე . @card@ წელი საქართველო სსრ შინაგანი საქმე მინისტრი . @card@ წელი აირჩევს საქართველო კომპარტიის ცკ-ის პირველი მდ

### Stage6: Training own model

optional: to clean disk space, we remove the downloaded file

In [ ]:
# optional: to clean disk space, we remove the downloaded file
!rm index.html\?dl\=1

In [ ]:
from gensim.test.utils import datapath
from gensim import utils

class MyCorpus:
    """An iterator that yields sentences (lists of str)."""

    def __iter__(self):
        corpus_path = datapath('myOwnLangText8.txt')
        for line in open(corpus_path):
            # assume there's one document per line, tokens separated by whitespace
            yield utils.simple_preprocess(line)

In [ ]:
import gensim.models
corpusOwn = MyCorpus()

optional: examining what is in the corpus after standard preprocessing

In [ ]:
# Optional: Examining our corpus format
type(corpusOwn)

__main__.MyCorpus

In [ ]:
dataOwn = [d for d in corpusOwn]

In [ ]:
print(len(dataOwn))
print(dataOwn[0])
print(len(dataOwn[0]))
print(dataOwn[4])
print(len(dataOwn[4]))
print(dataOwn[5])
print(len(dataOwn[5]))

1806
['ედუარდი', 'შევარდნაძე', 'ედუარდი', 'ამბროსის', 'ძე', 'შევარდნაძე', 'იანვარი', 'card', 'მამათი', 'დღევანდელი', 'ლანჩხუთის', 'მუნიციპალიტეტი', 'card', 'ივლისი', 'თბილისი', 'ქართველი', 'პოლიტიკოსი', 'და', 'სახელმწიფო', 'მოღვაწე', 'card', 'წელი', 'საბჭო', 'კავშირი', 'საგარეო', 'საქმე', 'მინისტრი', 'card', 'წელი', 'საქართველო', 'პრეზიდენტი', 'სკკპ', 'წევრი', 'card', 'წელი', 'card', 'წელი', 'ივლის', 'ოქტომბერში', 'მუშაობს', 'საქართველო', 'ალკკ', 'თბილისი', 'ორჯონიკიძის', 'რაიკომი', 'ინსტრუქტორად', 'ix', 'xi', 'მოწვევების', 'უმაღლესი', 'საბჭო', 'დეპუტატი', 'სოციალისტური', 'შრომა', 'გმირი', 'card', 'სკკპ', 'ცკ', 'ის', 'პოლიტბიუროს', 'წევრობა', 'კანდიდატი', 'card', 'წევრი', 'წელი', 'ივლისი', 'card', 'წელი', 'არის', 'საქართველო', 'სსრ', 'ის', 'კომკავშირის', 'პირველი', 'მდივანი', 'card', 'წელი', 'კომპარტიის', 'მცხეთის', 'რაიონული', 'კომიტეტი', 'პირველი', 'მდივანი', 'ხოლო', 'შემდეგ', 'თბილისი', 'პირველი', 'მაისი', 'რაიონი', 'რაიკომი', 'მდივანი', 'card', 'წელი', 'არის', 'კომპარტიის', 'ცენტრა

... Initialising global parameters for our modelL vector size, collocation window, skip-grams, negative sampling....

In [ ]:
from gensim.models import Word2Vec # The word2vec model class
import gensim.downloader as api # Allows us to download some free training data

In [ ]:
vector_size = 100 # Dimensionality of the word vectors
window = 5 # How many words either side? (5 = 5 context words either side, i.e. 10 context words in total)
use_skip_gram = 1 # If you set this to 0, then it will create a 'continuous bag of words' model instead
use_softmax = 0 # If you set this to 1, then hierarchical softmax will be used instead of negative sampling
negative_samples = 5 # How many incorrect answers to generate per correct answer when negative sampling

modelOwn = Word2Vec(
    size=vector_size,
    window=window,
    sg=use_skip_gram,
    hs=use_softmax,
    negative=negative_samples
)

... this cell may run for ~2 min or so...

In [ ]:
modelOwn.build_vocab(corpusOwn)

THIS MAY TAKE LONG!!! ... training the model may take 9 to 15 minutes... (just grab a cup of coffee or a sandwich while you are waiting... You may try chaning the number of epochs; if the number is lower the training is faster, but the quality may be lower...

In [ ]:
modelOwn.train(sentences=corpusOwn, epochs=5, total_examples=modelOwn.corpus_count)

(59378395, 70859245)

Now we copy word vectors and remove the model from memory (just to free up the resources...)

In [ ]:
word_vectors_own = modelOwn.wv

In [ ]:
del modelOwn

Now we can examine the output of our word embeddings

### Georgian examples

In [ ]:
# See the word vector for a particular word -- 'world'
vector = word_vectors_own['სამყარო']
print(vector)

[-0.62176156  0.23949477 -0.5179568   1.001093   -0.12505919  0.23363337
  0.36481667 -0.33915916 -0.06151456 -0.15845872  0.1443672   0.35141632
  0.41165924  0.5007546   0.04449251  0.6967667  -0.27176398  0.05205816
  0.27029327  0.20663835 -0.36598527 -0.14222133  0.16173883 -0.08235938
 -0.5496693  -0.15209736  0.48121738 -0.15404233  0.8891668   0.76310915
 -0.3202305  -0.18489017  0.3939411   0.15373786  0.02998169  0.20106426
 -0.0862966  -0.50034994 -0.05873515 -0.24013674  0.12750806  0.17326556
 -0.29788643  0.68244714 -0.21748939 -0.42120582  0.13775422 -0.35998118
  0.36402082  0.10524762 -0.0595954   0.3082781  -0.263306   -0.60933733
 -0.21795647 -0.04971887  0.09330089  0.01892476 -0.49159762 -0.11128791
 -0.30394047 -0.82244855 -0.48691386 -0.17550847 -0.15397266 -0.08480422
 -0.20583957 -0.67179024  0.77594376 -0.4534941   0.0747933   0.30824754
 -0.17382185 -0.47079867 -0.27730626  0.18782099 -0.10516048  0.51495117
  0.23847543 -0.11177064  0.04745216  0.10895227 -0

In [ ]:
# See which words are closest to a given word in the vector space = 'world'
similar_words = word_vectors_own.most_similar('არსება', topn=30)
print('\n'.join([str(tup) for tup in similar_words]))

('არსების', 0.8350973129272461)
('არსებები', 0.8056425452232361)
('დემონები', 0.8028587102890015)
('არსებებს', 0.8012523651123047)
('არსებებად', 0.7943331003189087)
('არსებად', 0.789718747138977)
('არსებანი', 0.7854664325714111)
('არსებაა', 0.7757723331451416)
('გეა', 0.7722355723381042)
('ყოვლისშემძლე', 0.7706775665283203)
('არსებების', 0.7645055055618286)
('სულები', 0.7611775994300842)
('მოკვდავი', 0.7600510120391846)
('დემონებზე', 0.754485011100769)
('ღმერთებზე', 0.7539801597595215)
('ლოპარების', 0.7538608312606812)
('კარმას', 0.7527127265930176)
('არსებათა', 0.7514225840568542)
('ჰუმანოიდური', 0.7510616183280945)
('სხეულისგან', 0.747897744178772)
('ადამიან', 0.7469550371170044)
('ღმერთები', 0.7469128370285034)
('არსებაზე', 0.7454417943954468)
('ღმერთია', 0.7444026470184326)
('სულებისა', 0.7416738271713257)
('მოგიზგიზე', 0.7412869334220886)
('სილამაზესა', 0.7398790121078491)
('ობობის', 0.7397568821907043)
('მსგავსს', 0.7365857362747192)
('მრავალთავიანი', 0.736303448677063)


In [ ]:
# blue
similar_words = word_vectors_own.most_similar('ლურჯი', topn=30) 
print('\n'.join([str(tup) for tup in similar_words]))

('თეთრი', 0.8326250910758972)
('მწვანე', 0.8310437202453613)
('ფერი', 0.8173065185546875)
('ყვითელი', 0.8154611587524414)
('წითელი', 0.8072329759597778)
('ოქროსფერი', 0.8043473958969116)
('ცისფერ', 0.8018262386322021)
('ვარდისფერი', 0.7977309823036194)
('ოქროსფერ', 0.7818973660469055)
('ფერებია', 0.7646973133087158)
('იასამნისფერი', 0.7630882263183594)
('ვერცხლისფერი', 0.7574926018714905)
('მუქი', 0.754925549030304)
('ცისფერი', 0.7541515827178955)
('სტაფილოსფერი', 0.7397026419639587)
('თეთრ', 0.7386224269866943)
('ფერებშია', 0.7350391745567322)
('ნარინჯისფერი', 0.7323054671287537)
('ფერებად', 0.7321016788482666)
('წითელ', 0.7310094833374023)
('შორტები', 0.7249136567115784)
('იისფერი', 0.7244935035705566)
('ვერცხლისფერ', 0.7243334054946899)
('ფერისაა', 0.7218009233474731)
('ფერით', 0.7189768552780151)
('ყავისფერი', 0.7142767906188965)
('ნახევარმთვარე', 0.7126744389533997)
('მოწითალო', 0.7084356546401978)
('იისფერ', 0.7074872255325317)
('ნარინჯისფერ', 0.7070273160934448)


In [ ]:
# france
similar_words = word_vectors_own.most_similar('საფრანგეთი', topn=10)
print('\n'.join([str(tup) for tup in similar_words]))

In [ ]:
# x is to king as woman is to man
analogous_words = word_vectors_own.most_similar(negative=['კაცი'], positive=['მეფე','ქალი'])
print('\n'.join([str(tup) for tup in analogous_words]))

('დედოფალი', 0.7610162496566772)
('ფარაონის', 0.6152430772781372)
('მეფეების', 0.6116519570350647)
('სამეფო', 0.6032817363739014)
('დედოფლად', 0.5937286615371704)
('ამენჰოტეპ', 0.5872259140014648)
('სეთი', 0.5852410197257996)
('მეფეა', 0.577671229839325)
('მემკვიდრის', 0.5736474990844727)
('სტიუარტების', 0.5730718970298767)


In [ ]:
# x is to king as woman is to man
# x = small + biggest - big
# 𝑥−𝑣𝑒𝑐𝑡𝑜𝑟(′𝑠𝑚𝑎𝑙𝑙′)=𝑣𝑒𝑐𝑡𝑜𝑟(′𝑏𝑖𝑔𝑔𝑒𝑠𝑡′)−𝑣𝑒𝑐𝑡𝑜𝑟(′𝑏𝑖𝑔′) 
# ∴ 𝑥=𝑣𝑒𝑐𝑡𝑜𝑟(′𝑠𝑚𝑎𝑙𝑙′)+𝑣𝑒𝑐𝑡𝑜𝑟(′𝑏𝑖𝑔𝑔𝑒𝑠𝑡′)−𝑣𝑒𝑐𝑡𝑜𝑟(′𝑏𝑖𝑔′) 
# ∴ 𝑥=𝑣𝑒𝑐𝑡𝑜𝑟(′փոքր′)+𝑣𝑒𝑐𝑡𝑜𝑟(′ամենամեծը′)−𝑣𝑒𝑐𝑡𝑜𝑟(′մեծ′) 
analogous_words = word_vectors_own.most_similar(negative=['პირი'], positive=['ხალხი','ქალიშვილი'])
print('\n'.join([str(tup) for tup in analogous_words]))

In [ ]:
# try your own examples... (also -- morphology?)
# # x is to daughter as people is to person (plural + daughter)
# analogous_words = word_vectors.most_similar(negative=['person'], positive=['people','daughter'])

### Armenian examples

In [ ]:
# See the word vector for a particular word -- 'world'
vector = word_vectors_own['աշխարհը']
print(vector)

In [ ]:
# See which words are closest to a given word in the vector space = 'world'
similar_words = word_vectors_own.most_similar('աշխարհը', topn=10)
print('\n'.join([str(tup) for tup in similar_words]))

In [ ]:
# blue
similar_words = word_vectors_own.most_similar('կապույտ', topn=10) 
print('\n'.join([str(tup) for tup in similar_words]))

In [ ]:
# france
similar_words = word_vectors_own.most_similar('ֆրանսիա', topn=10)
print('\n'.join([str(tup) for tup in similar_words]))

In [ ]:
# x is to king as woman is to man
analogous_words = word_vectors_own.most_similar(negative=['մարդ'], positive=['թագավոր','կին'])
print('\n'.join([str(tup) for tup in analogous_words]))

In [ ]:
# x is to king as woman is to man
# x = small + biggest - big
# 𝑥−𝑣𝑒𝑐𝑡𝑜𝑟(′𝑠𝑚𝑎𝑙𝑙′)=𝑣𝑒𝑐𝑡𝑜𝑟(′𝑏𝑖𝑔𝑔𝑒𝑠𝑡′)−𝑣𝑒𝑐𝑡𝑜𝑟(′𝑏𝑖𝑔′) 
# ∴ 𝑥=𝑣𝑒𝑐𝑡𝑜𝑟(′𝑠𝑚𝑎𝑙𝑙′)+𝑣𝑒𝑐𝑡𝑜𝑟(′𝑏𝑖𝑔𝑔𝑒𝑠𝑡′)−𝑣𝑒𝑐𝑡𝑜𝑟(′𝑏𝑖𝑔′) 
# ∴ 𝑥=𝑣𝑒𝑐𝑡𝑜𝑟(′փոքր′)+𝑣𝑒𝑐𝑡𝑜𝑟(′ամենամեծը′)−𝑣𝑒𝑐𝑡𝑜𝑟(′մեծ′) 
analogous_words = word_vectors_own.most_similar(negative=['մեծ'], positive=['ամենամեծը','փոքր'])
print('\n'.join([str(tup) for tup in analogous_words]))

In [ ]:
# try your own examples... (also -- morphology?)
# # x is to daughter as people is to person (plural + daughter)
# analogous_words = word_vectors.most_similar(negative=['person'], positive=['people','daughter'])